We will insert the downloaded data into databases

In [66]:
import psycopg2
import pandas as pd
import os
import json

connection = psycopg2.connect("dbname=publibike_db user=publibike_user")
cursor = connection.cursor()


bikedatapath = os.path.join("Bicincitta_Drop", "datasets_2013")
stnfile = file(os.path.join(bikedatapath, "stations.json"), "r")
subnetfile =  file(os.path.join(bikedatapath, "subnetworks.json"), "r")             
userfile =  file(os.path.join(bikedatapath, "users.json"), "r")                       
trxnfile =  file(os.path.join(bikedatapath, "transactions.json"), "r")                       





In [ ]:
subnets = json.load(subnetfile)[u'RECORDS']

for snet in subnets:
    i = int(snet[u'id'])
    name = snet[u'name'].encode("utf8")
    cursor.execute("INSERT INTO bicincitta.subnetworks ( id, name) " +
                   "VALUES (%s, %s) ", (i, name))
connection.commit()

In [67]:
stations = json.load(stnfile)[u'RECORDS']

for statn in stations:
    i = int(statn[u'id'])
    lat = float(statn[u'latitude'])
    lon = float(statn[u'longitude'])
    name = statn[u'name']
    sid = int(statn[u'subnetwork_id'])
    #print (i, name, sid, lat, lon)
    cursor.execute("INSERT INTO bicincitta.stations (id," +
                   "name," + 
                   "subnetwork_id," + 
                   "latitude," + 
                   "longitude) " + 
                   "VALUES (%s, %s, %s, %s, %s)",
                   (i, name.encode("utf8"), sid, lat, lon))
connection.commit()
stnfle.close()

IntegrityError: duplicate key value violates unique constraint "stations_pkey"
DETAIL:  Key (id)=(145) already exists.


In [118]:
userfile =  file(os.path.join(bikedatapath, "users.json"), "r")        
users = json.load(userfile)[u'RECORDS']
userfile.close()

connection = psycopg2.connect("dbname=publibike_db user=publibike_user")
cursor = connection.cursor()
cursor.execute("DELETE FROM bicincitta.users")

for user in users:
    adr = user[u'address']
    exp = user[u'expires']
    exp = None if exp == "" else exp
    gnd = user[u'gender']
    i = int(user[u'id'])
    pc = user[u'postal_code']
    sid = int(user[u'subnetwork_id'])
    if sid != 2005 and sid != 2011:
        cursor.execute("INSERT INTO bicincitta.users (id, "+
                                                      "subnetwork_id,"+
                                                      "gender,"+
                                                      "postal_code,"+
                                                      "address,"+
                                                      "expires)"+
                       "VALUES(%s, %s, %s, %s, %s, %s)",
                       (i, sid, gnd, pc, adr, exp))
connection.commit()
                   
    

In [119]:
len(users)

83874

In [112]:
u2005 = [ u for u in users if u['subnetwork_id'] == u'2005']
u2005ids = set([u['id'] for u in u2005])
u2011 = [ u for u in users if u['subnetwork_id'] == u'2011']
u2011ids = set([u['id'] for u in u2011])
uidsvalid = set([u['id'] for u in users]).difference( u2005ids.union(u2011ids))
usids = set([u['subnetwork_id'] for u in users])
ssids = set([s['subnetwork_id'] for s in stations])

In [115]:
trxn2005 = [ trxn for trxn in trxns if trxn[u'user_id'] in  u2005ids]
trxn2011 = [ trxn for trxn in trxns if trxn[u'user_id'] in  u2011ids]
trxnvalid = [trxn for trxn in trxns if trxn[u'user_id'] in uidsvalid]

In [123]:
len(trxns), len(trxn2005), len(trxn2011)

(291134, 0, 0)

In [124]:
subnets

[{u'id': u'1', u'name': u'La Cote'},
 {u'id': u'3', u'name': u'Bulle'},
 {u'id': u'4', u'name': u'Les Lacs-Romont'},
 {u'id': u'5', u'name': u'B\xe2le'},
 {u'id': u'13', u'name': u'PubliBike'},
 {u'id': u'10', u'name': u'Campus'},
 {u'id': u'15', u'name': u'Morges'},
 {u'id': u'16', u'name': u'Ouchy'},
 {u'id': u'17', u'name': u'Paradiso'},
 {u'id': u'18', u'name': u'Cern'},
 {u'id': u'14', u'name': u'Vevey'},
 {u'id': u'2', u'name': u'Agglo Fribourg'},
 {u'id': u'8', u'name': u'Yverdon-les-Bains'},
 {u'id': u'12', u'name': u'Lugano-Paradiso'},
 {u'id': u'7', u'name': u'Valais Central'},
 {u'id': u'6', u'name': u'Chablais'},
 {u'id': u'9', u'name': u'Lausanne-Morges'},
 {u'id': u'11', u'name': u'Riviera'}]

In [120]:
trxnfile =  file(os.path.join(bikedatapath, "transactions.json"), "r") 
trxns = json.load(trxnfile)[u'RECORDS']
trxnfile.close()

connection = psycopg2.connect("dbname=publibike_db user=publibike_user")
cursor = connection.cursor()
cursor.execute("DELETE FROM bicincitta.transactions")
for trxn in trxns:
    drxn = "OUT" if (trxn[u'direction'] == "check_out") else "IN"
    i = int(trxn[u'id'])
    t = trxn[u'event_time']
    uid = int(trxn[u'user_id'])
    sid = int(trxn[u'station_id'])
    cursor.execute( "INSERT INTO bicincitta.transactions ( id, " + 
                                                           "timestamp," +
                                                           "user_id," +
                                                           "station_id," + 
                                                           "direction)" +
                   "VALUES (%s, %s, %s, %s, %s)",
                   (i, t, uid, sid, drxn))
connection.commit()
                                                            

In [121]:
len(trxns)

291134

The subnetworks in the *subnetworks* data set do not correspond to the real subnetworks as we think of them:

In [270]:
subnets_df = pd.DataFrame(subnets)
subnets_df.index = subnets_df.id
subnets_df.head()

id             name
id                     
1    1          La Cote
3    3            Bulle
4    4  Les Lacs-Romont
5    5             Bâle
13  13        PubliBike

As we can see *Ouchy* is a subnetwork ! But there is no station for subnetwork *Ouchy*.
Lets look at what subnetwork_ids are available in stations,

In [155]:
station_sids = set([s['subnetwork_id'] for s in stations])

def sidStnOverlap(i, j):
    si = set([s[u'id'] for s in stations if s[u'subnetwork_id'] == i])
    sj = set([s[u'id'] for s in stations if s[u'subnetwork_id'] == j])
    return si.intersection(sj)
    

In [159]:
for i in station_sids:
    print "overlap", i, i, sidStnOverlap(i, i)

overlap 11 11 set([u'183', u'186', u'187', u'184', u'185'])
overlap 10 10 set([u'203', u'206', u'172', u'163', u'168', u'169', u'162', u'164', u'165', u'166', u'167', u'160', u'161', u'171', u'170'])
overlap 12 12 set([u'201', u'198', u'207', u'211', u'194', u'197', u'191', u'190', u'193', u'192', u'210', u'188', u'189'])
overlap 1 1 set([u'151', u'195', u'108', u'120', u'132', u'131', u'109', u'111', u'110', u'113', u'112', u'119', u'107'])
overlap 3 3 set([u'128', u'129'])
overlap 2 2 set([u'200', u'142', u'143', u'133', u'114', u'117', u'116', u'199', u'115', u'118'])
overlap 4 4 set([u'123', u'202', u'121', u'122', u'130', u'124', u'125', u'126', u'127'])
overlap 7 7 set([u'146', u'147', u'144', u'145', u'150', u'196', u'148'])
overlap 6 6 set([u'140', u'141', u'159', u'149', u'137', u'136', u'135', u'134', u'139', u'138'])
overlap 9 9 set([u'208', u'182', u'180', u'181', u'179', u'178', u'177', u'176', u'175', u'174', u'173'])
overlap 8 8 set([u'153', u'152', u'155', u'154', u'157

In [162]:
def stationsInSubnet(i):
    return [(s['id'], s['name']) for s in stations if s['subnetwork_id'] == i]

In [167]:
stationsInSubnet('6')

[(u'141', u'Centre Manor - Monthey'),
 (u'134', u'Gare d\xb4Aigle'),
 (u'135', u'Hotel de Ville - Aigle'),
 (u'136', u'Zone industrielle'),
 (u'138', u'Place du Cotterg'),
 (u'139', u'Site Chimique - Monthey'),
 (u'140', u'Hotel de Ville - Monthey'),
 (u'137', u'Place de la Gare - Monthey'),
 (u'149', u'Piscine - Aigle'),
 (u'159', u'Avenue de l\xb4Europe - Monthey')]

In [130]:
lm_stations = [s for s in stations if s[u'subnetwork_id'] == u'9']

In [133]:
[s for s in stations if s[u'name'] == u'Ouchy']

[{u'id': u'161',
  u'latitude': u'46.50687010769493',
  u'longitude': u'6.625957489013672',
  u'name': u'Ouchy',
  u'subnetwork_id': u'10'}]

In [138]:
station_sids = set([s['subnetwork_id'] for s in stations])
station_sids

{u'1', u'10', u'11', u'12', u'2', u'3', u'4', u'6', u'7', u'8', u'9'}

In [343]:
trxn_uids = list(set([ t[u'user_id'] for t in trxns]))
print "the number of users who have registered a transaction", len(trxn_uids)

the number of users who have registered a transaction 8952


#Closure of transactions.

To see if all the transactions we need to sort the transactions by their event time.
After that we define a function that maps the time sorted transactions of a user to a sequence of -1 (out) and +1 (in). A cummulative sum of this sequence will then tell us if the transactions are closed.

In [191]:
from datetime import datetime
trxns = sorted(trxns, 
               key = lambda t: datetime.strptime(t['event_time'], "%m/%d/%Y %H:%M:%S"))

In [223]:
import numpy as np
def outinTrace(uid):
    utrxns = [ t['direction'] for t in trxns if t['user_id'] == uid]
    outin = np.cumsum([ -1 if t == 'check-out' else +1 for t in utrxns])
    return outin
def closedTrxnChecker(uid):
    outin = outinTrace(uid)
    return {'user': uid, 'min': np.min(outin), 'max': np.max(outin)}

In [207]:
trxnClosures = [closedTrxnChecker(uid) for uid in trxn_uids]

Now that we have min/max for the closure of transactions for each user, we can look at how many/ which users have non-closing transactions. 

In [215]:
print "how large can transaction non-closure index get ?", set(t['max'] for t in trxnClosures)

how large can transaction non-closure index get ? set([0, 1, 2, 3, 4, 6, 7, 8, 9, 13])


In [216]:
print "how small can transaction non-closure index get ?",set(t['min'] for t in trxnClosures)

how small can transaction non-closure index get ? set([0, -11, -23, -21, -19, -18, -17, -16, -15, -14, -13, -12, -2, -10, -9, -8, -7, -6, -5, -4, -3, -1])


This means that there are some users who have taken upto 23 bikes out before returning any! This may be OK, but then there are some users who have returned 13 bikes without renting any! Next, lets look at these delinquent cases, who are they?

In [227]:
delinquentUsers = [t['user'] for t in trxnClosures if t['max'] > 0 or t['min'] < -1]

In [242]:
u = 1
uid = delinquentUsers[u]
tru =  outinTrace(uid)
i = np.argmax(tru) if closedTrxnChecker(uid)['max'] > 0 else np.argmin(tru)
pd.DataFrame([t for t in trxns if t['user_id'] == delinquentUsers[u]][i-2: i + 2 ])

created_at  direction           event_time      id  \
0  04/29/2015 10:43:19.343392   check-in  06/05/2013 07:25:38  542838   
1  04/29/2015 10:43:48.500096  check-out  06/05/2013 17:19:42  544185   
2  04/29/2015 10:43:48.589129  check-out  06/05/2013 17:20:47  544189   
3  04/29/2015 10:43:48.593881   check-in  06/05/2013 17:27:21  544190   

  station_id                  updated_at user_id  
0        109  04/29/2015 10:43:19.343392   91686  
1        109  04/29/2015 10:43:48.500096   91686  
2        109  04/29/2015 10:43:48.589129   91686  
3        108  04/29/2015 10:43:48.593881   91686

In [248]:
print "What subnetwork do delinquent users use",
set([u['subnetwork_id'] for u in users if u['id'] in delinquentUsers])

What subnetwork do delinquent users use

{u'13'}

The subnetwork 13 is the id for Publibike! What about the stations that the delinquent users use?

In [254]:
delinq_stns = set([t['station_id'] for t in trxns if t['user_id'] in delinquentUsers])

In [251]:
pd.DataFrame([s for s in stations if s['id'] == u'109'])

id   latitude longitude         name subnetwork_id
0  109  46.425959  6.287804  La Ligniere             1

In [305]:
list(subnets_df.name[list(delinq_stns_df.subnetwork_id)])

[u'Campus',
 u'Yverdon-les-Bains',
 u'Campus',
 u'Lugano-Paradiso',
 u'Lausanne-Morges',
 u'Yverdon-les-Bains',
 u'Lugano-Paradiso',
 u'Lugano-Paradiso']

In [302]:
delinq_stns_df

id            latitude          longitude            name subnetwork_id
0  203           46.523023           6.565379   Quartier nord            10
1  205          46.7736538          6.6356867            CPNV             8
2  206           46.532962           6.566493        Ecublens            10
3  207   46.00995862060886   8.95334243774414         Morcote            12
4  208             46.5058             6.6711          Paudex             9
5  209  46.777964883682365  6.639086540722701        P+R+BIKE             8
6  211   46.00995862060886   8.95334243774414    Mulino Nuovo            12
7  210   46.00995862060886   8.95334243774414  Arte e Cultura            12

In [307]:
non_delinq_stns_df = pd.DataFrame( s for s in stations if s['id'] not in delinq_stns)
non_delinq_stns_df['subnetwork_name'] = list(subnets_df.name[ list(delinq_stns_df.subnetwork_id)])
non_delinq_stns_df

id            latitude          longitude            name subnetwork_id  \
0  203           46.523023           6.565379   Quartier nord            10   
1  205          46.7736538          6.6356867            CPNV             8   
2  206           46.532962           6.566493        Ecublens            10   
3  207   46.00995862060886   8.95334243774414         Morcote            12   
4  208             46.5058             6.6711          Paudex             9   
5  209  46.777964883682365  6.639086540722701        P+R+BIKE             8   
6  211   46.00995862060886   8.95334243774414    Mulino Nuovo            12   
7  210   46.00995862060886   8.95334243774414  Arte e Cultura            12   

     subnetwork_name  
0             Campus  
1  Yverdon-les-Bains  
2             Campus  
3    Lugano-Paradiso  
4    Lausanne-Morges  
5  Yverdon-les-Bains  
6    Lugano-Paradiso  
7    Lugano-Paradiso

In [310]:
delinq_stns_df = pd.DataFrame( s for s in stations if s['id']  in delinq_stns)
delinq_stns_df['subnetwork_name'] = list(subnets_df.name[ list(delinq_stns_df.subnetwork_id)])
delinq_stns_df.head()

id            latitude          longitude                    name  \
0  145  46.228466314214494  7.350518703460693            Ancien-Stand   
1  147  46.230767099149595  7.373178005218506             Bietschhorn   
2  141            46.26061            6.94682  Centre Manor - Monthey   
3  134            46.31715            6.96444            Gare d´Aigle   
4  135           46.317696           6.969498  Hotel de Ville - Aigle   

  subnetwork_id subnetwork_name  
0             7  Valais Central  
1             7  Valais Central  
2             6        Chablais  
3             6        Chablais  
4             6        Chablais

We saw that the *subnetwork_id* assigned to the users was 13 (PubliBike) for delinquent users. However when we looked at the stations used by the delinquent users we see that the subnetwork assingned to those stations is not Publibike (13)!!! **We observe that neither the subnetwork provided in the data set, nor the subnetwork_id in the users data set are usable, as in they do not match the subnetwork_ids in stations, or transactions.**

It may be that the *subnetwork_id* assigned to stations means something different from the *subnetwork_id* assigned to the users. What do the *subnetwork_id*s assigned to stations correspond to, assuming that the *subnetwork* dataset is meaningful?

In [314]:
stn_df = pd.DataFrame(stations)
stn_df['subnetwork_name'] = list(subnets_df.name[list(stn_df.subnetwork_id)])
stn_df

id            latitude           longitude  \
0    145  46.228466314214494   7.350518703460693   
1    147  46.230767099149595   7.373178005218506   
2    141            46.26061             6.94682   
3    134            46.31715             6.96444   
4    135           46.317696            6.969498   
5    136           46.317577            6.938199   
6    138           46.253886            6.946634   
7    139           46.254871            6.959761   
8    140           46.251006            6.946066   
9    144   46.23225142534453   7.363629341125488   
10   146    46.2356355389661  7.3600029945373535   
11   148  46.227709260664696   7.358951568603516   
12   116           46.802646            7.150946   
13   117            46.81727             7.15727   
14   118           46.793455            7.158424   
15   107  46.420098079820974   6.268982291221619   
16   108           46.420176            6.270525   
17   109           46.425959            6.287804   
18   110           46.384008            6.234907   
19   111           46.394083            6.249786   
20   112           46.383101            6.226063   
21   113           46.382844            6.244033   
22   114           46.793089            7.132370   
23   115           46.780511            7.150608   
24   119           46.399568            6.231995   
25   120            46.42239            6.258305   
26   121           46.848714            6.846416   
27   122            46.84519             6.84457   
28   123            46.88505             7.04190   
29   124           46.925589            7.115654   
..   ...                 ...                 ...   
74   177           46.510625            6.482135   
75   189   46.00572598721853   8.961796760559082   
76   210   46.00995862060886    8.95334243774414   
77   156   46.77167325673971  6.6474151611328125   
78   155  46.778109947323905   6.641278266906738   
79   152   46.78522174258489   6.646857261657715   
80   153   46.78148963659166   6.646599769592285   
81   154   46.78113698327711   6.640677452087402   
82   157  46.764853640279114   6.645998954772949   
83   158   46.77875651298518  6.6581010818481445   
84   173           46.512980            6.614156   
85   174    46.5280441838176    6.59119606018066   
86   175    46.5259478163088    6.60282611846924   
87   178           46.515134            6.487965   
88   180    46.5088269146711    6.49928212165833   
89   181           46.502229            6.481164   
90   182    46.5178568507295    6.52772426605225   
91   183    46.4627678994401    6.84182167053223   
92   184    46.4654726816927    6.83508664369583   
93   185           46.456180            6.853485   
94   186           46.451157            6.859172   
95   187           46.468174            6.842806   
96   190   45.99096885257084   8.943665027618408   
97   191  45.985020167375254   8.931970596313477   
98   192           46.023191            8.959956   
99   193           46.010590            8.958023   
100  194           46.017556            8.956008   
101  196    46.2308710032899   7.353179454803467   
102  188           46.005202            8.952499   
103  176    46.5108574889387    6.49397134780884   

                                       name subnetwork_id    subnetwork_name  
0                              Ancien-Stand             7     Valais Central  
1                               Bietschhorn             7     Valais Central  
2                    Centre Manor - Monthey             6           Chablais  
3                              Gare d´Aigle             6           Chablais  
4                    Hotel de Ville - Aigle             6           Chablais  
5                         Zone industrielle             6           Chablais  
6                          Place du Cotterg             6           Chablais  
7                   Site Chimique - Monthey             6           Chablais  
8                  Hotel de Ville - Monthey             6           Ch

In [321]:
stn_df[stn_df.subnetwork_name == u'Campus']

id           latitude          longitude                      name  \
53  203          46.523023           6.565379             Quartier nord   
55  206          46.532962           6.566493                  Ecublens   
60  165   46.5190602366659     6.562260389328         Place Alan Turing   
61  167   46.5227588204584   6.58522009849548                   Dorigny   
62  164          46.522151           6.564859                    Rivier   
63  168          46.522146           6.579089               Unil Centre   
64  160   46.5204260105004   6.63050651550293         Place de l’Europe   
65  163          46.520714           6.568706            Avenue Piccard   
66  166          46.520902           6.573317                     Sorge   
67  169          46.526102           6.577892                    IDHEAP   
68  162   46.5374620761177     6.581711769104           Place du Marché   
69  172   46.5369602233686    6.5778923034668            Gare de Renens   
70  161  46.50687010769493  6.625957489013672                     Ouchy   
71  170   46.5175320057859   6.56132698059082  Quartier de l’Innovation   
72  171          46.519876           6.579682  Centre Sportif UNIL EPFL   

   subnetwork_id subnetwork_name  
53            10          Campus  
55            10          Campus  
60            10          Campus  
61            10          Campus  
62            10          Campus  
63            10          Campus  
64            10          Campus  
65            10          Campus  
66            10          Campus  
67            10          Campus  
68            10          Campus  
69            10          Campus  
70            10          Campus  
71            10          Campus  
72            10          Campus

In [322]:
stn_df

id            latitude           longitude  \
0    145  46.228466314214494   7.350518703460693   
1    147  46.230767099149595   7.373178005218506   
2    141            46.26061             6.94682   
3    134            46.31715             6.96444   
4    135           46.317696            6.969498   
5    136           46.317577            6.938199   
6    138           46.253886            6.946634   
7    139           46.254871            6.959761   
8    140           46.251006            6.946066   
9    144   46.23225142534453   7.363629341125488   
10   146    46.2356355389661  7.3600029945373535   
11   148  46.227709260664696   7.358951568603516   
12   116           46.802646            7.150946   
13   117            46.81727             7.15727   
14   118           46.793455            7.158424   
15   107  46.420098079820974   6.268982291221619   
16   108           46.420176            6.270525   
17   109           46.425959            6.287804   
18   110           46.384008            6.234907   
19   111           46.394083            6.249786   
20   112           46.383101            6.226063   
21   113           46.382844            6.244033   
22   114           46.793089            7.132370   
23   115           46.780511            7.150608   
24   119           46.399568            6.231995   
25   120            46.42239            6.258305   
26   121           46.848714            6.846416   
27   122            46.84519             6.84457   
28   123            46.88505             7.04190   
29   124           46.925589            7.115654   
..   ...                 ...                 ...   
74   177           46.510625            6.482135   
75   189   46.00572598721853   8.961796760559082   
76   210   46.00995862060886    8.95334243774414   
77   156   46.77167325673971  6.6474151611328125   
78   155  46.778109947323905   6.641278266906738   
79   152   46.78522174258489   6.646857261657715   
80   153   46.78148963659166   6.646599769592285   
81   154   46.78113698327711   6.640677452087402   
82   157  46.764853640279114   6.645998954772949   
83   158   46.77875651298518  6.6581010818481445   
84   173           46.512980            6.614156   
85   174    46.5280441838176    6.59119606018066   
86   175    46.5259478163088    6.60282611846924   
87   178           46.515134            6.487965   
88   180    46.5088269146711    6.49928212165833   
89   181           46.502229            6.481164   
90   182    46.5178568507295    6.52772426605225   
91   183    46.4627678994401    6.84182167053223   
92   184    46.4654726816927    6.83508664369583   
93   185           46.456180            6.853485   
94   186           46.451157            6.859172   
95   187           46.468174            6.842806   
96   190   45.99096885257084   8.943665027618408   
97   191  45.985020167375254   8.931970596313477   
98   192           46.023191            8.959956   
99   193           46.010590            8.958023   
100  194           46.017556            8.956008   
101  196    46.2308710032899   7.353179454803467   
102  188           46.005202            8.952499   
103  176    46.5108574889387    6.49397134780884   

                                       name subnetwork_id    subnetwork_name  
0                              Ancien-Stand             7     Valais Central  
1                               Bietschhorn             7     Valais Central  
2                    Centre Manor - Monthey             6           Chablais  
3                              Gare d´Aigle             6           Chablais  
4                    Hotel de Ville - Aigle             6           Chablais  
5                         Zone industrielle             6           Chablais  
6                          Place du Cotterg             6           Chablais  
7                   Site Chimique - Monthey             6           Chablais  
8                  Hotel de Ville - Monthey             6           Ch

In [324]:
sum( [u['address'] != '' for u in users])

21659

In [325]:
len(users)

83874

## Who is using the network?


First we assign each user their trip, and use the resulting dict to compute some statistics for each user.


In [404]:
userTrxns = { uid: [] for uid in trxn_uids }
for t in trxns:
    uid = t[u'user_id']
    userTrxns[uid].append(t)
    

for user 84965 0
for user 84883 0
for user 84758 0
for user 84754 0
for user 106119 0
for user 106119 1
for user 106119 2
for user 88849 0
for user 88849 1
for user 87701 0
for user 87701 1
for user 87518 0
for user 88180 0
for user 85256 0
for user 88180 1
for user 85256 1
for user 85273 0
for user 84945 0
for user 88347 0
for user 84945 1
for user 84944 0
for user 85273 1
for user 85232 0
for user 88347 1
for user 84944 1
for user 85288 0
for user 88226 0
for user 88755 0
for user 91621 0
for user 85288 1
for user 86579 0
for user 88226 1
for user 88895 0
for user 91621 1
for user 88895 1
for user 88755 1
for user 88120 0
for user 86579 1
for user 86638 0
for user 84803 0
for user 84545 0
for user 84545 1
for user 84545 2
for user 85409 0
for user 88592 0
for user 102550 0
for user 102550 1
for user 87884 0
for user 102550 2
for user 102550 3
for user 84803 1
for user 88592 1
for user 91800 0
for user 84635 0
for user 84635 1
for user 88120 1
for user 85409 1
for user 85248 0
for use

In [405]:
userNumTrxns = { u: len(t) for u, t in userTrxns.iteritems() }

In [414]:
usersWithAdr = [u'id'] for u in users if u['address'] != '']
usersWithoutAdr = [u['id'] for u in users if u['address'] == '']

In [423]:
users[0]

{u'address': u'',
 u'expires': u'',
 u'gender': u'M',
 u'id': u'83875',
 u'postal_code': u'',
 u'subnetwork_id': u'13'}

In [424]:
userNumTrxns[u'83875']

KeyError: u'83875'